In [5]:
from google.colab import files

files.upload()

Saving circuits.csv to circuits.csv
Saving constructor_results.csv to constructor_results.csv
Saving constructor_standings.csv to constructor_standings.csv
Saving constructors.csv to constructors.csv
Saving driver_standings.csv to driver_standings.csv
Saving drivers.csv to drivers.csv
Saving pit_stops.csv to pit_stops.csv
Saving qualifying.csv to qualifying.csv
Saving races.csv to races.csv
Saving results.csv to results.csv
Saving seasons.csv to seasons.csv
Saving sprint_results.csv to sprint_results.csv
Saving status.csv to status.csv


{'circuits.csv': b'circuitId,circuitRef,name,location,country,lat,lng,alt,url\n1,"albert_park","Albert Park Grand Prix Circuit","Melbourne","Australia",-37.8497,144.968,10,"http://en.wikipedia.org/wiki/Melbourne_Grand_Prix_Circuit"\n2,"sepang","Sepang International Circuit","Kuala Lumpur","Malaysia",2.76083,101.738,18,"http://en.wikipedia.org/wiki/Sepang_International_Circuit"\n3,"bahrain","Bahrain International Circuit","Sakhir","Bahrain",26.0325,50.5106,7,"http://en.wikipedia.org/wiki/Bahrain_International_Circuit"\n4,"catalunya","Circuit de Barcelona-Catalunya","Montmel\xc3\xb3","Spain",41.57,2.26111,109,"http://en.wikipedia.org/wiki/Circuit_de_Barcelona-Catalunya"\n5,"istanbul","Istanbul Park","Istanbul","Turkey",40.9517,29.405,130,"http://en.wikipedia.org/wiki/Istanbul_Park"\n6,"monaco","Circuit de Monaco","Monte-Carlo","Monaco",43.7347,7.42056,7,"http://en.wikipedia.org/wiki/Circuit_de_Monaco"\n7,"villeneuve","Circuit Gilles Villeneuve","Montreal","Canada",45.5,-73.5228,13,"http:

In [6]:
import pandas as pd

Making a map from race ID to circuit ID

In [7]:
races_df= pd.read_csv('races.csv')
race_circuit_map= races_df[['raceId', 'circuitId']]

results_df: 'resultId','raceId','driverId','constructorId','number', 'grid','position', 'positionText', 'positionOrder, 'points', 'laps', 'time','milliseconds', 'fastestLap', 'rank', 'fastestLapTime','fastestLapSpeed', 'statusId'.

races_df: 'raceId', 'year', 'round', 'circuitId', 'name', 'date', 'time', 'url','fp1_date', 'fp1_time', 'fp2_date', 'fp2_time', 'fp3_date', 'fp3_time','quali_date', 'quali_time', 'sprint_date', 'sprint_time'

In [8]:
results_df= pd.read_csv('results.csv')

merged_result_df = results_df.merge(race_circuit_map, on='raceId', how='left')

feature1 = merged_result_df.groupby(['driverId', 'circuitId'], as_index=False)['grid'].mean().rename(columns={'grid': 'avgGridPosition'})

feature1['avgGridPosition'] = feature1['avgGridPosition'].round(2)
feature1

driverId  circuitId  avgGridPosition
0            1          1             4.29
1            1          2             5.09
2            1          3             4.22
3            1          4             4.37
4            1          5             6.29
...        ...        ...              ...
8266       865         39             4.00
8267       865         70            13.00
8268       865         73             8.00
8269       865         77            14.00
8270       865         79            11.00

[8271 rows x 3 columns]

In [10]:
driver_races = results_df.merge(races_df[['raceId', 'circuitId', 'year', 'round']], on='raceId', how='left')
driver_races = driver_races.sort_values(['driverId', 'year', 'round'])
driver_races["previous_race"]= (driver_races.groupby(['driverId', 'circuitId']).cumcount())

feature11= driver_races[['driverId', 'circuitId', 'previous_race']]

feature11[feature11['driverId'] == 1]

driverId  circuitId  previous_race
370           1          1              0
391           1          2              0
413           1          3              0
435           1          4              0
457           1          6              0
...         ...        ...            ...
27004         1         13             18
27029         1         11             18
27057         1         39              4
27063         1         14             18
27085         1         73              8

[373 rows x 3 columns]

Momentum_df: 'raceId', 'driverId', 'lap', 'position', 'time', 'milliseconds'

In [11]:
status_df= pd.read_csv('status.csv')
status_df

statusId          status
0           1        Finished
1           2    Disqualified
2           3        Accident
3           4       Collision
4           5          Engine
..        ...             ...
134       137          Damage
135       138          Debris
136       139         Illness
137       140       Undertray
138       141  Cooling system

[139 rows x 2 columns]

In [12]:
status_df= pd.read_csv('status.csv')
feature8= results_df.merge(status_df, on='statusId', how='left')
feature8['DNF']= feature8['status'].str.contains('Finished') == False
total_races = feature8.groupby('driverId')['raceId'].nunique().reset_index(name='total_races')
dnf_races = feature8[feature8['DNF']].groupby('driverId')['raceId'].nunique().reset_index(name='dnf_races')
driver_dnf_fraction = total_races.merge(dnf_races, on='driverId', how='left')
driver_dnf_fraction['dnf_races'] = driver_dnf_fraction['dnf_races'].fillna(0)
driver_dnf_fraction['dnf_fraction'] = driver_dnf_fraction['dnf_races'] / driver_dnf_fraction['total_races']

driver_dnf_fraction = driver_dnf_fraction.drop(["total_races",	"dnf_races"], axis=1)

driver_dnf_fraction

driverId  dnf_fraction
0           1      0.126005
1           2      0.641304
2           3      0.296117
3           4      0.353919
4           5      0.651786
..        ...           ...
859       861      0.600000
860       862      0.571429
861       863      0.352941
862       864      0.470588
863       865      0.411765

[864 rows x 2 columns]

In [13]:
rc_df= pd.read_csv('pit_stops.csv')
rc_df

raceId  driverId  stop  lap      time duration  milliseconds
0         841       153     1    1  17:05:23   26.898         26898
1         841        30     1    1  17:05:52   25.021         25021
2         841        17     1   11  17:20:48   23.426         23426
3         841         4     1   12  17:22:34   23.251         23251
4         841        13     1   13  17:24:10   23.842         23842
...       ...       ...   ...  ...       ...      ...           ...
11988    1161       846     1   37  16:13:07   21.975         21975
11989    1161       840     1   37  16:13:54    21.82         21820
11990    1161       852     1   38  16:14:50   20.323         20323
11991    1161       847     1   39  16:16:26   19.809         19809
11992    1161       830     1   40  16:17:58   20.221         20221

[11993 rows x 7 columns]